In [59]:
import branca.colormap as cm
import folium
import geopandas as gpd
import pandas as pd
from tqdm.auto import tqdm
tqdm.pandas()
import json

pd.set_option("display.max_columns", 100)

In [60]:
import os
import sys

import branca.colormap as cm
import numpy as np
import pandas as pd
from shapely.geometry import LineString, Point, Polygon

sys.path.insert(0, "../src")
import json
import time as ti
import math

import geopandas as gpd
import seaborn as sns
from sklearn import preprocessing
from tqdm import tqdm
import seaborn as sns 
from IPython.display import display, Math, Latex
import requests

from BrusselsMap import BrusselsMap
from GeoJsonHandler import GeoJsonHandler

pd.set_option("display.max_rows", 500)
pd.set_option("display.max_columns", 500)

## Geographical data

In [61]:
# GeoJson Shapefile
sectors_geo = r"../data/maps/stat_sectors/json/RBC_stat_sectors_2021.json"

# open the json 
with open(sectors_geo) as sectors_file:
    sectors_json = json.load(sectors_file)
    
# Extract names of each statistical sector in the city of Brussels (RBC)
names_json = []
for index in range(len(sectors_json["features"])):
    names_json.append(sectors_json["features"][index]["properties"]["Sector"])

## Values for Choropleth Map

In [62]:
population = pd.read_csv("../data/population/population_stats_sectors.csv")
population = population[["CD_SECTOR", "POPULATION"]]
population.rename(
    columns={"CD_SECTOR": "Stat_Sector", "POPULATION": "Population"}, inplace=True
)
population.head(5)

Stat_Sector  Population
0   11001A00-        2490
1   11001A01-        2755
2   11001A020         732
3   11001A030         431
4   11001A042         351

In [63]:
# Adding the population value to each sector of the geojson file
for index in tqdm(range(len(sectors_json["features"]))):

    temp_dict = sectors_json["features"][index]["properties"]
    temp_dict["Population"] = "Population: " + str(
        population[population["Stat_Sector"] == temp_dict["Sector"]]["Population"].item()
    )
    sectors_json["features"][index]["properties"] = temp_dict

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 724/724 [00:01<00:00, 411.75it/s]


## Generate Choropleth Map

In [64]:
# initial map coordinates
coords = [50.84892175574389, 4.3514911042124345]

world = folium.Map(
    location=[coords[0], coords[1]], zoom_start=12.45, tiles="stamenwatercolor"
)

choropleth = folium.Choropleth(
    geo_data=sectors_json,
    data=population,
    columns=["Stat_Sector", "Population"],
    # threshold_scale=threshold_scale,
    key_on="feature.properties.Sector",
    fill_color="YlOrRd",
    fill_opacity=0.25,
    line_opacity=0.5,
    # legend_name="Population in Region-Brussels-Capital",
    highlight=True,
    smooth_factor=0,
).add_to(world)

style_function = "font-size: 15px"
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(
        ["Sector"], style=style_function, labels=False
    )
)

for key in choropleth._children:
    if key.startswith('color_map'):
        del(choropleth._children[key])
        
choropleth.add_to(world)

world

In [65]:
o_path = r"../data/outputs/maps/"
world.save(os.path.join(o_path, "statistical-sectors-brussels.html")) # to HTML

## Neighborhood Level

In [66]:
# GeoJson Shapefile
sectors_geo = r"../data/final_data/sector.json"
population = pd.read_csv(r"../data/population/population.csv")

# open the json 
with open(sectors_geo) as sectors_file:
    sectors_json = json.load(sectors_file)

In [67]:
# initial map coordinates
coords = [50.84892175574389, 4.3514911042124345]

world = folium.Map(
    location=[coords[0], coords[1]], zoom_start=12.45, tiles="stamenwatercolor"
)

choropleth = folium.Choropleth(
    geo_data=sectors_json,
    data=population,
    columns=["NAME_FRE", "POP"],
    # threshold_scale=threshold_scale,
    key_on="feature.properties.NAME_FRE",
    fill_color="YlOrRd",
    fill_opacity=0.25,
    line_opacity=0.5,
    # legend_name="Population in Region-Brussels-Capital",
    highlight=True,
    smooth_factor=0,
).add_to(world)

style_function = "font-size: 15px"
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(
        ["NAME_FRE"], style=style_function, labels=False
    )
)

for key in choropleth._children:
    if key.startswith('color_map'):
        del(choropleth._children[key])
        
choropleth.add_to(world)

world

In [68]:
o_path = r"../data/outputs/maps/"
world.save(os.path.join(o_path, "neighborhoods-brussels.html")) # to HTML

## Municipality Level

In [91]:
# GeoJson Shapefile
sectors_geo = r"../data/municipalities/wfs.json"
population = pd.read_csv(r"../data/population/population.csv")

# open the json 
with open(sectors_geo) as sectors_file:
    sectors_json = json.load(sectors_file)
    
# Extract names of each statistical sector in the city of Brussels (RBC)
names_json = []
for index in range(len(sectors_json["features"])):
    names_json.append(sectors_json["features"][index]["properties"]["name_fr"])

In [92]:
dff = pd.DataFrame(names_json)
dff.rename(columns={0:'name_fr'}, inplace=True)
dff["VAL"] = np.random.randint(1000, size=len(dff))
dff.head()

name_fr  VAL
0             Anderlecht  447
1              Auderghem  245
2  Berchem-Sainte-Agathe  922
3                 Forest  134
4                  Jette  299

In [93]:
# Adding the population value to each sector of the geojson file
for index in tqdm(range(len(sectors_json["features"]))):

    temp_dict = sectors_json["features"][index]["properties"]
    temp_dict["Population"] = "Population: " + str(
        dff[dff["name_fr"] == temp_dict["name_fr"]]["VAL"].item()
    )
    sectors_json["features"][index]["properties"] = temp_dict

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 19/19 [00:00<00:00, 1197.80it/s]


In [94]:
# initial map coordinates
coords = [50.84892175574389, 4.3514911042124345]

world = folium.Map(
    location=[coords[0], coords[1]], zoom_start=12.45, tiles="stamenwatercolor"
)

choropleth = folium.Choropleth(
    geo_data=sectors_json,
    data=dff,
    columns=["name_fr", "VAL"],
    # threshold_scale=threshold_scale,
    key_on="feature.properties.name_fr",
    fill_color="YlOrRd",
    fill_opacity=0.25,
    line_opacity=0.5,
    # legend_name="Population in Region-Brussels-Capital",
    highlight=True,
    smooth_factor=0,
).add_to(world)

style_function = "font-size: 15px"
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(
        ["name_fr"], style=style_function, labels=False
    )
)

for key in choropleth._children:
    if key.startswith('color_map'):
        del(choropleth._children[key])
        
choropleth.add_to(world)

world

In [95]:
o_path = r"../data/outputs/maps/"
world.save(os.path.join(o_path, "municipalities-brussels.html")) # to HTML